In [17]:
import pandas as pd
import numpy as np
import re

In [54]:
# read csv
df = pd.read_csv('/home/arnau/Desktop/Cambridge/MARS/correctness-model-internals/evaluations/evaluations/llama3.3_70b/trivia_qa_2_60k/base/main_generations_evaluated.csv')
df.head()

prompt               answer  \
0  I am going to ask you a question. Answer conci...          Anna Neagle   
1  I am going to ask you a question. Answer conci...  Worcester Cathedral   
2  I am going to ask you a question. Answer conci...         Going to bed   
3  I am going to ask you a question. Answer conci...       Dombey and Son   
4  I am going to ask you a question. Answer conci...       James Braddock   

                                        ground_truth  correct  
0  ['Florence Marjorie Robertson' 'Anna Neagle' '...        1  
1  ['Prior of Worcester' 'Worcester Cathedral' 'W...        1  
2  ['BEDS' "Captain's bed" 'California king (bed)...        0  
3  ['DOMBEY AND SON' 'Dombey & Son' 'Dombey and s...        1  
4  ['James J Braddock' 'JAMES J BRADDOCK' 'James ...        0

In [55]:
df['correct_revisited'] = df['correct']
for index, row in df.iterrows():
    if row['correct'] == 0:
        # check if answer in the list of row['ground_truth']
        list_ans = re.findall(r"""['"]([^'"]+)['"]""", row['ground_truth'])
        for gt in list_ans:  # Updated to use list_ans instead of list(row['ground_truth'])
            if str(row['answer']).lower() in str(gt).lower() or str(gt).lower() in str(row['answer']).lower():
                df.at[index, 'correct_revisited'] = 1
                break

print("Before:", len(df[df['correct'] == 0])/len(df))
print("After:", len(df[df['correct_revisited'] == 0])/len(df))

Before: 0.23467017388036757
After: 0.0958904109589041


In [56]:
# save
df.to_csv('/home/arnau/Desktop/Cambridge/MARS/correctness-model-internals/evaluations/evaluations/llama3.3_70b/trivia_qa_2_60k/base/main_generations_evaluated_revisited.csv', index=False)

In [45]:
df

prompt               answer  \
0      I am going to ask you a question. Answer conci...     Marlene Dietrich   
1      I am going to ask you a question. Answer conci...            Worcester   
2      I am going to ask you a question. Answer conci...        Closed spaces   
3      I am going to ask you a question. Answer conci...       Dombey and Son   
4      I am going to ask you a question. Answer conci...    James J. Braddock   
...                                                  ...                  ...   
58541  I am going to ask you a question. Answer conci...         Mary Poppins   
58542  I am going to ask you a question. Answer conci...           The Hobbit   
58543  I am going to ask you a question. Answer conci...             A sucker   
58544  I am going to ask you a question. Answer conci...               Hawaii   
58545  I am going to ask you a question. Answer conci...  The Louvre in Paris   

                                            ground_truth  correct  \
0      ['Florence Marjorie Robertson' 'Anna Neagle' '...        0   
1      ['Prior of Worcester' 'Worcester Cathedral' 'W...        0   
2      ['BEDS' "Captain's bed" 'California king (bed)...        0   
3      ['DOMBEY AND SON' 'Dombey & Son' 'Dombey and s...        1   
4      ['James J Braddock' 'JAMES J BRADDOCK' 'James ...        1   
...                                                  ...      ...   
58541  ['Mrs. George Banks' 'Winifred banks' '17 Cher...        1   
58542  ['Little Hobbit' 'Giant (Middle-earth)'\n 'The...        0   
58543  ['Sucker (anatomy)' 'Suckering' 'Sucker' 'Suck...        0   
58544  ['Haiwii' 'The State of Hawaii' 'Mokuʻāina o H...        1   
58545  ['Salle des Etats' 'Musée du Louvre, Paris' 'M...        0   

       correct_revisited  
0                      0  
1                      1  
2                      1  
3                      1  
4                      1  
...                  ...  
58541                  1  
58542                  1  
58543                  1  
58544                  1  
58545                  1  

[58546 rows x 5 columns]

In [49]:
for index, row in df[df['correct_revisited'] == 0].iterrows():
    print("Question: ", row['prompt'][527:])
    print("Answer: ", row['answer'])
    print("True answer: ", row['ground_truth'])
    print()

Question:  Which actress was born Marjorie Robertson in 1904?
Answer:
Answer:  Marlene Dietrich
True answer:  ['Florence Marjorie Robertson' 'Anna Neagle' 'DAME ANNA NEAGLE'
 'Dame Anna Neagle' 'Neagle, Anna, Dame' 'Anna, Dame Neagle']

Question:  England beat Australia at Lords in 2009 for the first time at that venue since 1934. Who was the UK's Prime Minister then?
Answer:
Answer:  Gordon Brown
True answer:  ['James Ramsay MacDonald' 'Ramsay Macdonald' 'MacDonald, Ramsey'
 'Ramsay McDonald' 'MacDonald, Ramsay' 'James Ramsay Macdonald'
 'MacDonald, (James) Ramsay' '(James) Ramsay MacDonald' 'Ramsay MacDonald'
 'MacDonald, James Ramsay' 'Ramsey McDonald' 'Ramsay Mcdonald'
 'Ramsey MacDonald' 'RAMSEY McDONALD' 'James Ramsey MacDonald'
 'Ramsey Macdonald']

Question:  In Stevenson's Treasure Island, who was the coxswain of the Hispaniola?
Answer:
Answer:  Long John Silver
True answer:  ['Israel Hands' 'ISRAEL HANDS']

Question:  What name is given to a stone anchor and also colloquially

In [50]:
for index, row in df[(df['correct_revisited'] == 1) & (df['correct'] == 0)].iterrows():
    print("Question: ", row['prompt'][527:])
    print("Answer: ", row['answer'])
    print("True answer: ", row['ground_truth'])
    print()

Question:  The majority of English Monarchs since the Norman Conquest were interred in either Westminster or Windsor, but where was King John buried?
Answer:
Answer:  Worcester
True answer:  ['Prior of Worcester' 'Worcester Cathedral' 'Worcester Abbey'
 'Worcester Priory' 'Cathedral Church of Christ & St Mary, Worcester'
 'Worcester cathedral'
 'Cathedral Church of Christ and the Blessed Mary the Virgin of Worcester'
 'Worcester Cathedral Chamber Choir' 'Worcester Cathedral Priory'
 'WORCESTER CATHEDRAL' 'Worcester Cathedral Choir'
 "Worcester Cathedral St. Peter's Priory"
 'The Cathedral Church of Christ and the Blessed Mary the Virgin of Worcester']

Question:  A person who suffers from clinophobia is afraid of what?
Answer:
Answer:  Closed spaces
True answer:  ['BEDS' "Captain's bed" 'California king (bed)' 'Full size bed' 'Bedknobs'
 'Ottoman bed' 'Bed (furniture)' '🛏' '丬' 'Beds' 'Captain bed' 'Bed'
 'Cabin bed']

Question:  Of what is gymnophobia a fear?
Answer:
Answer:  The fear 